In [2]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import butter, TransferFunction, lsim, tf2zpk
from scipy import signal
from scipy.io import wavfile
from scipy.fft import fft,ifft
from IPython.display import Audio
from playsound import playsound

# Sampling frequency
Fs = 48000  # Standard audio sampling rate

def Impulse(duration, frequency, relative_amplitude, delay):
    a = 1 / duration
    omega = 2 * np.pi * frequency
    
    # Correct the transfer function coefficients
    numerator = [relative_amplitude * omega]
    denominator = [1, 2 * a, a ** 2 + omega ** 2]
    
    # Define and compute impulse response
    system = TransferFunction(numerator, denominator)
    t, h_almost = signal.impulse(system, T=np.linspace(0, 1, int(Fs)))
    
    # Add delay with padding
    h = np.concatenate((np.zeros(int(delay * Fs)), h_almost))
    return h[:int(0.5 * Fs)]  # Limit to 0.5 seconds

def bpm_more_signals(signal, BPM):
    BPS = BPM / 60  # Beats per second
    silence = np.zeros(int(Fs * (1 / BPS)))  # Silence between beats
    return np.tile(np.concatenate((signal, silence)), 10)

def zero_pad_arrays(t1,t2):
    mlen = max(map(len, [t1, t2,]))
    t1_new = np.concatenate((t1,np.zeros(mlen-len(t1))))
    t2_new = np.concatenate((t2,np.zeros(mlen-len(t2))))
    # t3_new = np.concatenate((t3,np.zeros(mlen-len(t3))))
    # t4_new = np.concatenate((t4,np.zeros(mlen-len(t4))))
    return t1_new, t2_new

# Generate impulse response and BPM signals
h_M = Impulse(0.02,150,1,0.01) # Generate single impulse response
h_T = Impulse(0.02,450,0.8,0.04)
h_A = Impulse(0.02,200,0.7,0.3)
h_P = Impulse(0.02,150,0.7,0.33)

h_M,h_T = zero_pad_arrays(h_M,h_T)
h_A,h_P = zero_pad_arrays(h_A,h_P)
h_Mbpm = bpm_more_signals(h_M, 60)  # Repeat signal with BPM structure
h_Tbpm = bpm_more_signals(h_T, 60)
h_Abpm = bpm_more_signals(h_A, 60)  # Repeat signal with BPM structure
h_Pbpm = bpm_more_signals(h_P, 60)

# Create stereo data
h_dual = np.stack([h_Mbpm, h_Tbpm], axis=-1)  # Stereo: shape (N, 2)
h_dual = np.asarray(h_dual, dtype=np.float32)  # Ensure proper data type

h_dual2 = np.stack([h_Abpm, h_Pbpm], axis=-1)  # Stereo: shape (N, 2)
h_dual2 = np.asarray(h_dual2, dtype=np.float32)  # Ensure proper data type


# Write WAV file
wavfile.write("S1.wav", Fs, h_dual)
wavfile.write("S2.wav", Fs, h_dual2)

# Play the WAV file
Audio("S1.wav",autoplay=False, rate=Fs)

